In [1]:
#Import libraries

import pandas as pd
import numpy as np
import os
import string
import nltk
from nltk.tokenize import word_tokenize
from bs4 import BeautifulSoup
import xml.etree.ElementTree as ET
import re
from nltk.tokenize import RegexpTokenizer

from gensim.models import Word2Vec
from sklearn.metrics.pairwise import cosine_similarity
from multiprocessing import Pool

from numpy import dot
from numpy.linalg import norm
import pickle

In [2]:
#nltk.download('stopwords')

In [3]:
df = pd.read_csv('small_db.csv')

In [4]:
df = df.dropna()
df.head(10)

Unnamed: 0  id                                              Codes  \
0           0   4  <code>decimal trans = trackBar1.Value / 5000;\...   
1           1   6  <code>div</code> <code>div</code> <code>percen...   
2           3   9                              <code>DateTime</code>   
3           4  11                              <code>DateTime</code>   
4           6  13                            <code>user-agent</code>   
5           7  14  <code>Math.Floor()</code> <code>Math.Truncate(...   
6           8  16  <code>DataSet</code> <code>DataTable</code> <c...   
7          11  19  <code>#define</code> <code>M_PI</code> <code>4...   
8          13  24  <code>trigger</code> <code>before the update</...   
9          14  25  <code>z/OS</code> <code>sys/socket.h</code> <c...   

                                                Tags  
0  c#, floating-point, type-conversion, double, d...  
1                     html, css, internet-explorer-7  
2                                 c#, .net, datetime  
3   c#, datetime, time, datediff, relative-time-span  
4  html, browser, timezone, user-agent, timezone-...  
5                                         .net, math  
6                   c#, linq, web-services, .net-3.5  
7  performance, algorithm, language-agnostic, uni...  
8                          mysql, database, triggers  
9                    c++, c, sockets, mainframe, zos

In [5]:
df.shape

(46730, 4)

In [6]:
df.describe()

Unnamed: 0             id
count   46730.000000   46730.000000
mean   276561.723390  405317.038177
std    140011.812439  193158.957762
min         0.000000       4.000000
25%    164925.500000  254976.750000
50%    285971.500000  423923.000000
75%    398781.000000  574808.000000
max    499985.000000  702451.000000

In [7]:
df.values

array([[0, 4,
        "<code>decimal trans = trackBar1.Value / 5000;\nthis.Opacity = trans;\n</code> <code>'decimal'</code> <code>'double'</code> <code>trans</code> <code>double</code>",
        'c#, floating-point, type-conversion, double, decimal'],
       [1, 6,
        '<code>div</code> <code>div</code> <code>percentage-based width</code> <code>div</code> <code>0 width</code> <code>pixel width</code> <code>pixel-based width</code>',
        'html, css, internet-explorer-7'],
       [3, 9, '<code>DateTime</code>', 'c#, .net, datetime'],
       ...,
       [499970, 702433, '<code>CursorManager</code>', 'apache-flex'],
       [499982, 702448,
        '<code>$timestamp = $rows[blogentry_date]; //Just an example of a query result\n$users_timeszone_code = TheFunctionI_NeedHelpCreating() // Hopefully collects users \n// timezone code, and converts it to a supported \n// timezone using date_default_timezone_set()??(just a guess)\nCreateDate($users_timeszone_code, $timestamp);\n</code> <cod

In [8]:
df.dtypes

Unnamed: 0     int64
id             int64
Codes         object
Tags          object
dtype: object

In [9]:

# Code Tag
df['Codes'] = [BeautifulSoup(text).get_text() for text in df['Codes'] ]
    

In [10]:
df.head(20)

Unnamed: 0   id                                              Codes  \
0            0    4  decimal trans = trackBar1.Value / 5000;\nthis....   
1            1    6  div div percentage-based width div 0 width pix...   
2            3    9                                           DateTime   
3            4   11                                           DateTime   
4            6   13                                         user-agent   
5            7   14                       Math.Floor() Math.Truncate()   
6            8   16  DataSet DataTable DataSet DataTable public sta...   
7           11   19  #define M_PI 4 * atan(1) atan(1) -fno-builtin ...   
8           13   24                          trigger before the update   
9           14   25  z/OS sys/socket.h AF_INET z/OS #ifdef z/OS #de...   
10          21   34  ByteArray // First non-working solution\nbyteA...   
11          22   36  BINARY_CHECKSUM SELECT CHECKSUM_AGG(BINARY_CHE...   
12          23   39                                         while true   
13          27   48  <form>\r\n  <!-- Put your cursor in this field...   
14          34   59  DataTable Name var names =\n    (from DataRow ...   
15          39   66                                   startIndex count   
16          42   72                                                 ri   
17          48   80  Create Table tRole (\n    roleID integer Prima...   
18          55   88  QueryPerformanceCounter BOOL QueryPerformanceC...   
19          66  109  DECLARE%20@S%20NVARCHAR(4000);SET%20@S=CAST(0x...   

                                                 Tags  
0   c#, floating-point, type-conversion, double, d...  
1                      html, css, internet-explorer-7  
2                                  c#, .net, datetime  
3    c#, datetime, time, datediff, relative-time-span  
4   html, browser, timezone, user-agent, timezone-...  
5                                          .net, math  
6                    c#, linq, web-services, .net-3.5  
7   performance, algorithm, language-agnostic, uni...  
8                           mysql, database, triggers  
9                     c++, c, sockets, mainframe, zos  
10                arrays, actionscript-3, apache-flex  
11                  sql, sql-server, datatable, rdbms  
12                            c#, .net, vb.net, timer  
13            html, forms, form-submit, submit-button  
14                                 c#, linq, .net-3.5  
15                                     linq, .net-3.5  
16                                         ruby, rdoc  
17                   apache-flex, actionscript-3, air  
18             linux, winapi, visual-c++, unix, timer  
19                        c#, sql, vb.net, ascii, hex

In [11]:
df.head(20)

Unnamed: 0   id                                              Codes  \
0            0    4  decimal trans = trackBar1.Value / 5000;\nthis....   
1            1    6  div div percentage-based width div 0 width pix...   
2            3    9                                           DateTime   
3            4   11                                           DateTime   
4            6   13                                         user-agent   
5            7   14                       Math.Floor() Math.Truncate()   
6            8   16  DataSet DataTable DataSet DataTable public sta...   
7           11   19  #define M_PI 4 * atan(1) atan(1) -fno-builtin ...   
8           13   24                          trigger before the update   
9           14   25  z/OS sys/socket.h AF_INET z/OS #ifdef z/OS #de...   
10          21   34  ByteArray // First non-working solution\nbyteA...   
11          22   36  BINARY_CHECKSUM SELECT CHECKSUM_AGG(BINARY_CHE...   
12          23   39                                         while true   
13          27   48  <form>\r\n  <!-- Put your cursor in this field...   
14          34   59  DataTable Name var names =\n    (from DataRow ...   
15          39   66                                   startIndex count   
16          42   72                                                 ri   
17          48   80  Create Table tRole (\n    roleID integer Prima...   
18          55   88  QueryPerformanceCounter BOOL QueryPerformanceC...   
19          66  109  DECLARE%20@S%20NVARCHAR(4000);SET%20@S=CAST(0x...   

                                                 Tags  
0   c#, floating-point, type-conversion, double, d...  
1                      html, css, internet-explorer-7  
2                                  c#, .net, datetime  
3    c#, datetime, time, datediff, relative-time-span  
4   html, browser, timezone, user-agent, timezone-...  
5                                          .net, math  
6                    c#, linq, web-services, .net-3.5  
7   performance, algorithm, language-agnostic, uni...  
8                           mysql, database, triggers  
9                     c++, c, sockets, mainframe, zos  
10                arrays, actionscript-3, apache-flex  
11                  sql, sql-server, datatable, rdbms  
12                            c#, .net, vb.net, timer  
13            html, forms, form-submit, submit-button  
14                                 c#, linq, .net-3.5  
15                                     linq, .net-3.5  
16                                         ruby, rdoc  
17                   apache-flex, actionscript-3, air  
18             linux, winapi, visual-c++, unix, timer  
19                        c#, sql, vb.net, ascii, hex

In [12]:
#regex
df.replace([r"\\t|\\n|\\r", "\t|\n|\r"], value=["",""], regex=True , inplace=True)


In [13]:
df.head(20)

Unnamed: 0   id                                              Codes  \
0            0    4  decimal trans = trackBar1.Value / 5000;this.Op...   
1            1    6  div div percentage-based width div 0 width pix...   
2            3    9                                           DateTime   
3            4   11                                           DateTime   
4            6   13                                         user-agent   
5            7   14                       Math.Floor() Math.Truncate()   
6            8   16  DataSet DataTable DataSet DataTable public sta...   
7           11   19  #define M_PI 4 * atan(1) atan(1) -fno-builtin ...   
8           13   24                          trigger before the update   
9           14   25  z/OS sys/socket.h AF_INET z/OS #ifdef z/OS #de...   
10          21   34  ByteArray // First non-working solutionbyteArr...   
11          22   36  BINARY_CHECKSUM SELECT CHECKSUM_AGG(BINARY_CHE...   
12          23   39                                         while true   
13          27   48  <form>  <!-- Put your cursor in this field and...   
14          34   59  DataTable Name var names =    (from DataRow dr...   
15          39   66                                   startIndex count   
16          42   72                                                 ri   
17          48   80  Create Table tRole (    roleID integer Primary...   
18          55   88  QueryPerformanceCounter BOOL QueryPerformanceC...   
19          66  109  DECLARE%20@S%20NVARCHAR(4000);SET%20@S=CAST(0x...   

                                                 Tags  
0   c#, floating-point, type-conversion, double, d...  
1                      html, css, internet-explorer-7  
2                                  c#, .net, datetime  
3    c#, datetime, time, datediff, relative-time-span  
4   html, browser, timezone, user-agent, timezone-...  
5                                          .net, math  
6                    c#, linq, web-services, .net-3.5  
7   performance, algorithm, language-agnostic, uni...  
8                           mysql, database, triggers  
9                     c++, c, sockets, mainframe, zos  
10                arrays, actionscript-3, apache-flex  
11                  sql, sql-server, datatable, rdbms  
12                            c#, .net, vb.net, timer  
13            html, forms, form-submit, submit-button  
14                                 c#, linq, .net-3.5  
15                                     linq, .net-3.5  
16                                         ruby, rdoc  
17                   apache-flex, actionscript-3, air  
18             linux, winapi, visual-c++, unix, timer  
19                        c#, sql, vb.net, ascii, hex

In [14]:
df.head()

Unnamed: 0  id                                              Codes  \
0           0   4  decimal trans = trackBar1.Value / 5000;this.Op...   
1           1   6  div div percentage-based width div 0 width pix...   
2           3   9                                           DateTime   
3           4  11                                           DateTime   
4           6  13                                         user-agent   

                                                Tags  
0  c#, floating-point, type-conversion, double, d...  
1                     html, css, internet-explorer-7  
2                                 c#, .net, datetime  
3   c#, datetime, time, datediff, relative-time-span  
4  html, browser, timezone, user-agent, timezone-...

In [15]:
data_list_codes=[]
data_list_tags =[]

In [16]:
tokenizer = RegexpTokenizer(r'\w+')

tokenized_sents_codes = [tokenizer.tokenize(i) for i in df["Codes"]]
tokenized_sents_tags = [tokenizer.tokenize(j) for j in df["Tags"]]
for i in tokenized_sents_codes:
    print (i)
    data_list_codes.append(i)
for j in tokenized_sents_tags:
    print(j)
    data_list_tags.append(j)    

['decimal', 'trans', 'trackBar1', 'Value', '5000', 'this', 'Opacity', 'trans', 'decimal', 'double', 'trans', 'double']
['div', 'div', 'percentage', 'based', 'width', 'div', '0', 'width', 'pixel', 'width', 'pixel', 'based', 'width']
['DateTime']
['DateTime']
['user', 'agent']
['Math', 'Floor', 'Math', 'Truncate']
['DataSet', 'DataTable', 'DataSet', 'DataTable', 'public', 'static', 'MyDataTable', 'CallMySproc', 'string', 'conn', 'MyDatabaseDataContext', 'db', 'new', 'MyDatabaseDataContext', 'conn', 'MyDataTable', 'dt', 'new', 'MyDataTable', 'execute', 'a', 'sproc', 'via', 'LINQ', 'var', 'query', 'from', 'dr', 'in', 'db', 'MySproc', 'AsEnumerable', 'select', 'dr', 'copy', 'LINQ', 'query', 'resultset', 'into', 'a', 'DataTable', 'this', 'does', 'not', 'work', 'dt', 'query', 'CopyToDataTable', 'return', 'dt', 'DataSet', 'DataTable']
['define', 'M_PI', '4', 'atan', '1', 'atan', '1', 'fno', 'builtin', 'atan2', '0', '1', 'pitimes', 'c', 'include', 'math', 'h', 'include', 'stdio', 'h', 'include'

['xml', 'version', '1', '0', 'encoding', 'UTF', '8', 'standalone', 'yes', 'assembly', 'xmlns', 'urn', 'schemas', 'microsoft', 'com', 'asm', 'v1', 'manifestVersion', '1', '0', 'trustInfo', 'xmlns', 'urn', 'schemas', 'microsoft', 'com', 'asm', 'v3', 'security', 'requestedPrivileges', 'requestedExecutionLevel', 'level', 'asInvoker', 'uiAccess', 'false', 'requestedPrivileges', 'security', 'trustInfo', 'dependency', 'dependentAssembly', 'assemblyIdentity', 'type', 'win32', 'name', 'Microsoft', 'VC90', 'DebugCRT', 'version', '9', '0', '21022', '8', 'processorArchitecture', 'x86', 'publicKeyToken', '1fc8b3b9a1e18e3b', 'dependentAssembly', 'dependency', 'assembly']
['SELECT', 'x', 'query', 'FROM', 'xml', 'nodes', 'Books', 'not', 'ID', 'or', 'ID', '5', 'x1', 'x', 'DECLARE', 'Xml', 'XML', 'SET', 'Xml', 'N', 'Library', 'Novels', 'Novel', 'category', '1', 'Novel1', 'Novel', 'Novel', 'category', '2', 'Novel2', 'Novel', 'Novel', 'Novel3', 'Novel', 'Novel', 'category', '4', 'Novel4', 'Novel', 'Novels

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['behaviors', 'endpointBehaviors', 'behavior', 'name', 'Test2', 'dataContractSerializer', 'maxItemsInObjectGraph', '2147483647', 'behavior', 'endpointBehaviors', 'serviceBehaviors', 'behavior', 'name', 'serviceBehaviour', 'serviceDebug', 'includeExceptionDetailInFaults', 'true', 'serviceMetadata', 'serviceMetadata', 'httpGetEnabled', 'true', 'dataContractSerializer', 'maxItemsInObjectGraph', '2147483647', 'behavior', 'serviceBehaviors', 'behaviors', 'bindings', 'customBinding', 'binding', 'name', 'TestBinding2', 'inactivityTimeout', '00', '30', '00', 'openTimeout', '00', '30', '00', 'receiveTimeout', '00', '30', '00', 'sendTimeout', '00', '30', '00', 'binaryMessageEncoding', 'tcpTransport', 'transferMode', 'StreamedResponse', 'binding', 'customBinding', 'bindings']
['Testpublic', 'void', 'truthTest', 'assertTrue', 'true', 'Ok', 'Testpublic', 'void', 'truthTest', 'assertTrue', 'false', 'ERROR']
['public', 'class', 'Handle', 'private', 'String', 'handle', 'public', 'Handle', 'String', 'n

['php', 'rss']
['sql', 'database', 'sqlite', 'metadata']
['c', 'net', 'collections', 'iteration']
['c', 'asp', 'net', 'javascript', 'validation']
['sql', 'sorting']
['java', 'testing', 'junit', 'integration', 'testing']
['sql', 'server', 'reporting', 'services']
['html', 'css', 'internet', 'explorer']
['sql', 'server', 'ms', 'access', 'access', 'vba', 'ado']
['ruby', 'on', 'rails', 'caching']
['hibernate', 'postgresql', 'insert', 'database', 'partitioning']
['winapi']
['c', 'oracle']
['file', 'directory', 'filesystems', 'solaris']
['java', 'memory', 'performance']
['java', 'xml', 'xmlbeans']
['c', 'net']
['layout', 'html', 'css']
['wpf', 'browser', 'z', 'index']
['php', 'string']
['javascript']
['c', 'sql', 'sql', 'server']
['sql', 'sql', 'server', 'tsql']
['c', 'algorithm', 'math', 'np', 'complete']
['c', 'conditional', 'operator']
['ios', 'objective', 'c']
['oracle']
['php', 'oop', 'php', '5', '3', 'php', '5', '2']
['php', 'arrays', 'printing', 'foreach', 'get']
['c', 'gcc']
['python

...

['python', 'process', 'subprocess', 'stdout', 'popen']
['c', 'email', 'binary', 'attachment', 'system', 'net', 'mail']
['c', 'pointers', 'pinvoke']
['android', 'android', 'contacts', 'android', 'contentresolver']
['php', 'xmlreader']
['jquery', 'css']
['database']
['css']
['security', 'weblogic', 'jndi']
['html', 'mobile', 'internationalization']
['asp', 'net', 'mvc']
['installer', 'nsis']
['objective', 'c', 'xcode', 'macos']
['c', 'boost', 'boost', 'bind', 'boost', 'function']
['c', 'xml', 'well', 'formed']
['python', 'multithreading']
['c', 'net', 'casting', 'nullable']
['jquery', 'redirect', 'simplemodal']
['javascript', 'jquery', 'resize']
['c', 'net', 'datetime', 'date']
['javascript', 'dhtml']
['c', 'enums', 'constraints']
['sharepoint', 'wss', '3', '0']
['c', 'command', 'line', 'powershell', 'scripting', 'arguments']
['strong', 'typing', 'granularity']
['sql', 'sql', 'server', 'tsql']
['c', 'dynamic', 'data']
['fluent', 'nhibernate']
['c', 'wpf', 'data', 'binding', 'dependency',

['c', 'arrays', 'memory', 'stack', 'allocation']
['html', 'css']
['java', 'logging', 'log4j']
['python', 'django', 'sqlite', 'concurrency']
['matlab', 'matrix', 'matrix', 'indexing']
['django', 'django', 'admin', 'tinymce']
['svn']
['android', 'listview', 'focus']
['javascript']
['windows', 'regex', 'utilities']
['iphone', 'objective', 'c', 'cocoa', 'cocoa', 'touch']
['java', 'performance', 'scripting', 'code', 'cleanup']
['asp', 'net', 'webforms']
['regex', 'perl', 'pcre']
['javascript', 'jquery', 'ajax', 'prototypejs']
['bash', 'shell', 'error', 'handling']
['iphone', 'audio']
['c', 'class', 'instantiation']
['python', 'django', 'checkbox']
['c', 'net', 'asp', 'net', 'mvc']
['iphone', 'objective', 'c', 'cocoa', 'touch']
['html', 'css', 'text', 'word', 'wrap']
['jquery', 'ui', 'hash']
['servlets', 'cookies', 'encoding']
['version', 'control', 'project', 'management', 'code', 'organization', 'project', 'organization']
['svn']
['c', 'syntax', 'static']
['git', 'git', 'add']
['java']
['p

['java', 'tomcat', 'jar', 'manifest']
['c', 'silverlight', 'clr', 'postsharp', 'cil']
['php', 'htaccess', 'mod', 'rewrite', 'url', 'rewriting']
['vb', 'net']
['sql', 'sql', 'server', '2005', 'ms', 'access', 'ms', 'access', '2007']
['c', 'dependency', 'injection', 'inversion', 'of', 'control']
['javascript', 'oop', 'callback', 'definition']
['net', 'performance', 'data', 'structures', 'caching', 'lru']
['kindle']
['c', 'multithreading', 'winapi', 'multicore', 'interlocked']
['objective', 'c', 'boolean']
['svn', 'import', 'backup', 'visualsvn', 'visualsvn', 'server']
['regex', 'algorithm', 'language', 'agnostic', 'graphics']
['latex', 'ms', 'word', 'comments']
['wpf', 'navigation']
['c', 'net', 'vb', 'net', 'regex', 'parsing']
['c', 'keyboard', 'sendkeys']
['php', 'linux', 'email']
['c', 'net', 'winforms', 'user', 'controls']
['sql', 'mysql', 'truncate', 'self', 'reference']
['javascript', 'css', 'padding', 'margin', 'offset']
['iphone', 'objective', 'c', 'cocoa', 'touch', 'mobile']
['wp

['perl', 'conditional']
['python', 'setuptools']
['c', 'templates', 'switch', 'statement', 'chain', 'of', 'responsibility']
['jquery', 'ui']
['iphone', 'html', 'objective', 'c', 'cocoa', 'touch', 'escaping']
['php', 'download', 'stream']
['php', 'apache', 'htaccess', 'security', 'file', 'upload']
['ruby', 'syntax', 'identifier']
['sql', 'server', 'tsql', 'default', 'alter', 'table']
['css']
['wpf', 'combobox', 'data', 'binding']
['javascript', 'html', 'reorderlist']
['java', 'c', 'xml', 'serialization']
['apache', 'flex', 'actionscript', '3']
['java', 'multithreading']
['java', 'regex']
['python', 'django']
['c', 'net', 'multithreading', 'synchronization']
['mysql']
['python']
['asp', 'net', 'jquery', 'asp', 'net', 'mvc', 'json']
['python', 'multiprocessing']
['c', 'indexing', 'sorting']
['c', 'architecture']
['java', 'xml', 'inheritance', 'annotations', 'jaxb']
['c', 'char']
['visual', 'studio', 'visual', 'studio', '2005', 'cil']
['sql', 'sql', 'server', 'tsql', 'jsp', 'jdbc']
['c', '

['html', 'css']
['asp', 'net', 'null', 'httprequest']
['net', 'arrays', 'type', 'conversion']
['linq', 'linq', 'to', 'objects', 'llblgenpro']
['sql', 'mysql', 'generator']
['visual', 'studio', 'sharepoint', 'sharepoint', '2007', 'caml']
['c', 'boost', 'pointers', 'shared', 'ptr']
['perl', 'directory']
['python', 'try', 'catch']
['javascript', 'jquery', 'row', 'html', 'table', 'hidden', 'field']
['c', 'vb', 'net']
['bash', 'file', 'shell', 'random']
['c', 'outlook']
['c', 'asp', 'net', 'html', 'css']
['c', 'linq', 'linq', 'to', 'xml']
['iis', 'deployment', 'web', 'applications']
['javascript', 'html', 'user', 'input']
['c']
['hibernate', 'nhibernate', 'mapping', 'mapping']
['asp', 'net', 'download', 'page', 'lifecycle']
['distributed', 'cache']
['php']
['php', 'amazon', 'ec2', 'amazon', 's3', 'detect']
['sql', 'postgresql', 'npgsql']
['javascript', 'html', 'dom']
['c', 'net', 'winapi']
['c']
['asp', 'net', 'javascript', 'jquery', 'tablesorter']
['c', 'net', 'arrays', 'duplicates']
['xml

In [17]:
data_list_codes

[['decimal',
  'trans',
  'trackBar1',
  'Value',
  '5000',
  'this',
  'Opacity',
  'trans',
  'decimal',
  'double',
  'trans',
  'double'],
 ['div',
  'div',
  'percentage',
  'based',
  'width',
  'div',
  '0',
  'width',
  'pixel',
  'width',
  'pixel',
  'based',
  'width'],
 ['DateTime'],
 ['DateTime'],
 ['user', 'agent'],
 ['Math', 'Floor', 'Math', 'Truncate'],
 ['DataSet',
  'DataTable',
  'DataSet',
  'DataTable',
  'public',
  'static',
  'MyDataTable',
  'CallMySproc',
  'string',
  'conn',
  'MyDatabaseDataContext',
  'db',
  'new',
  'MyDatabaseDataContext',
  'conn',
  'MyDataTable',
  'dt',
  'new',
  'MyDataTable',
  'execute',
  'a',
  'sproc',
  'via',
  'LINQ',
  'var',
  'query',
  'from',
  'dr',
  'in',
  'db',
  'MySproc',
  'AsEnumerable',
  'select',
  'dr',
  'copy',
  'LINQ',
  'query',
  'resultset',
  'into',
  'a',
  'DataTable',
  'this',
  'does',
  'not',
  'work',
  'dt',
  'query',
  'CopyToDataTable',
  'return',
  'dt',
  'DataSet',
  'DataTable'],

In [18]:
data_list_tags

[['c', 'floating', 'point', 'type', 'conversion', 'double', 'decimal'],
 ['html', 'css', 'internet', 'explorer', '7'],
 ['c', 'net', 'datetime'],
 ['c', 'datetime', 'time', 'datediff', 'relative', 'time', 'span'],
 ['html', 'browser', 'timezone', 'user', 'agent', 'timezone', 'offset'],
 ['net', 'math'],
 ['c', 'linq', 'web', 'services', 'net', '3', '5'],
 ['performance', 'algorithm', 'language', 'agnostic', 'unix', 'pi'],
 ['mysql', 'database', 'triggers'],
 ['c', 'c', 'sockets', 'mainframe', 'zos'],
 ['arrays', 'actionscript', '3', 'apache', 'flex'],
 ['sql', 'sql', 'server', 'datatable', 'rdbms'],
 ['c', 'net', 'vb', 'net', 'timer'],
 ['html', 'forms', 'form', 'submit', 'submit', 'button'],
 ['c', 'linq', 'net', '3', '5'],
 ['linq', 'net', '3', '5'],
 ['ruby', 'rdoc'],
 ['apache', 'flex', 'actionscript', '3', 'air'],
 ['linux', 'winapi', 'visual', 'c', 'unix', 'timer'],
 ['c', 'sql', 'vb', 'net', 'ascii', 'hex'],
 ['sql', 'asp', 'net', 'xml', 'sitemap'],
 ['java', 'xml', 'csv', 'data

In [19]:
final_data=[a + b for a, b in zip(data_list_codes, data_list_tags)]

In [20]:
final_data

[['decimal',
  'trans',
  'trackBar1',
  'Value',
  '5000',
  'this',
  'Opacity',
  'trans',
  'decimal',
  'double',
  'trans',
  'double',
  'c',
  'floating',
  'point',
  'type',
  'conversion',
  'double',
  'decimal'],
 ['div',
  'div',
  'percentage',
  'based',
  'width',
  'div',
  '0',
  'width',
  'pixel',
  'width',
  'pixel',
  'based',
  'width',
  'html',
  'css',
  'internet',
  'explorer',
  '7'],
 ['DateTime', 'c', 'net', 'datetime'],
 ['DateTime', 'c', 'datetime', 'time', 'datediff', 'relative', 'time', 'span'],
 ['user',
  'agent',
  'html',
  'browser',
  'timezone',
  'user',
  'agent',
  'timezone',
  'offset'],
 ['Math', 'Floor', 'Math', 'Truncate', 'net', 'math'],
 ['DataSet',
  'DataTable',
  'DataSet',
  'DataTable',
  'public',
  'static',
  'MyDataTable',
  'CallMySproc',
  'string',
  'conn',
  'MyDatabaseDataContext',
  'db',
  'new',
  'MyDatabaseDataContext',
  'conn',
  'MyDataTable',
  'dt',
  'new',
  'MyDataTable',
  'execute',
  'a',
  'sproc',
  


# Create and train model
- Create a word2vec model and train it with Hamlet corpus
- Key parameter description (https://radimrehurek.com/gensim/models/word2vec.html)
- sentences: training data (has to be a list with tokenized sentences)
- size: dimension of embedding space
- sg: CBOW if 0, skip-gram if 1
- window: number of words accounted for each context (if the window size is 3, 3 word in the left neighorhood and 3 word in the right neighborhood are considered)
- min_count: minimum count of words to be included in the vocabulary
- iter: number of training iterations
- workers: number of worker threads to train
# Default
- size: The number of dimensions of the embeddings and the default is 100.
- window: The maximum distance between a target word and words around the target word. The default window is 5.
- min_count: The minimum count of words to consider when training the model; words with occurrence less than this - - count will be ignored. The default for min_count is 5.
- workers: The number of partitions during training and the default workers is 3.
- sg: The training algorithm, either CBOW(0) or skip gram (1). The default training alogrithm is CBOW

In [21]:
model = Word2Vec(sentences = final_data, size = 100, sg = 1, window = 3, min_count = 1, iter = 10, workers = Pool()._processes)

Process ForkPoolWorker-7:
Process ForkPoolWorker-1:
Process ForkPoolWorker-2:
Process ForkPoolWorker-8:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/towhidur/anaconda3/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/towhidur/anaconda3/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/towhidur/anaconda3/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/towhidur/anaconda3/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/towhidur/anaconda3/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/towhidur/anaconda3/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/towhidur/an

In [22]:
model.init_sims(replace = True)

# Save and load model
- word2vec model can be saved and loaded locally
- Doing so can reduce time to train model again

In [23]:
model.save('word2vec_model')

In [24]:
model = Word2Vec.load('word2vec_model')

# Similarity calculation
- Similarity between embedded words (i.e., vectors) can be computed using metrics such as cosine similarity
- For other metrics and comparisons between them, refer to: https://github.com/taki0112/Vector_Similarity

In [25]:
## We can obtain the word embedding directly from the training model


#model.wv.__getitem__('html')

In [26]:
#Now we could even use Word2vec to compute similarity between two make model in the vocabulary by invoking the model.similarity() and passing in the relvevant words.
#This will give us the Euclidian similarity 


#model.wv.similarity('html', 'css')

In [27]:
## Show the most similar for html : Default by eculidean distance 

#model.wv.most_similar('html') [:3]

In [28]:
'''
def create_dictionary(final_data):
    euclid_dictionary={}
    for item in final_data:
        for word in item:
            top3 = model.wv.most_similar(word)[:3]
            items_list = []
            for items in top3:
                items_list.append(str(items[0])+"-"+str(items[1]))
            euclid_dictionary[word] = items_list
    return euclid_dictionary
            
 '''          

'\ndef create_dictionary(final_data):\n    euclid_dictionary={}\n    for item in final_data:\n        for word in item:\n            top3 = model.wv.most_similar(word)[:3]\n            items_list = []\n            for items in top3:\n                items_list.append(str(items[0])+"-"+str(items[1]))\n            euclid_dictionary[word] = items_list\n    return euclid_dictionary\n            \n '

In [29]:
'''
def find_synonym(input_text,dictionary):
    for k,v in dictionary.items():
        if k == input_text:
            for val in v:
                print(val)
'''

'\ndef find_synonym(input_text,dictionary):\n    for k,v in dictionary.items():\n        if k == input_text:\n            for val in v:\n                print(val)\n'

In [30]:
#Euclidean Distance Dictionary creation, comment it out for creating new dictionary

#euclid_dict = create_dictionary(final_data)

# Pickling

In [31]:
# Save a dictionary into a pickle file(serialization)


#pickle.dump(euclid_dict, open("./euclid_dict.p", "wb"))  # save it into a file named euclid_dict.p'''

## Unpickling

In [32]:
# Load the dictionary back from the pickle file.(unserialization)


#unserialized_euclid_dict = pickle.load(open("./euclid_dict.p", "rb"))

In [33]:

#find_synonym("html",unserialized_euclid_dict)

# Cosine Similarity

In [34]:
def create_dictionary_cosmul(final_data):
    euclid_dictionary_cosmul={}
    for item in final_data:
        for word in item:
            top3 = model.wv.most_similar_cosmul(word)[:3]
            items_list = []
            for items in top3:
                items_list.append(str(items[0])+"-"+str(items[1]))
            euclid_dictionary_cosmul[word] = items_list
    return euclid_dictionary_cosmul

In [35]:
euclid_dict_cosmul = create_dictionary_cosmul(final_data)

KeyboardInterrupt: 

In [82]:
# Save Pickle file

pickle.dump(euclid_dict_cosmul, open("./euclid_dict_cosmul.p", "wb"))

In [83]:
unserialized_euclid_dict_cosmul = pickle.load(open("./euclid_dict_cosmul.p", "rb"))

In [90]:
find_synonym("python",unserialized_euclid_dict_cosmul)

build-0.9948590397834778
system-0.994772732257843
parsing-0.9946872591972351
